## Reinforcement Learning

Reinforcement learning is one of three basic machine learning paradigms, alongside supervised learning and unsupervised learning.

"Reinforcement learning differs from supervised learning in not needing labelled input/output pairs be presented, and in not needing sub-optimal actions to be explicitly corrected. Instead the focus is on finding a balance between exploration (of uncharted territory) and exploitation (of current knowledge)"

In the coming chapters we are going to learn about reinforcement learning approaches

- Markov Decision Processes
- Q Learning
- Deep Q Learning

These are typical reinforcement learning techniques. We don't have target variables (or labels) but the algorithms will figure out (and learn) the optimal strategies (when playing games such as chess or tic tac toe).

### Applications of Reinforcement Learning
1) Playing Games
  - Mario, Chess, or Go
2) Learning basically anything
  - Self-driving cars or how to fly
3) Finance: Q-learning algorithm is able to learn an optimal trading strategy with one simple instruction
  - Maimize the value of our portofolio
4) Logistics: Vehicle Routing Problem
- Reinforcement Learning + Deep Learning -> Extremely Powerful

## Markov Decsion Process

In machine learning, the environment is typically formulated as a <b>Markov Decision Process</b>. 
It is the extended version of a Markov Chain

1. Set of States: S
    - In chess, a state is a given configuration of the board
2. Set of Actions: A (e.g., up, down, left, right)
    -  Every possible move in chess or tic-tac-toe
3. Conditional distribution of the next state, the next state depends on the actual one exclusivly
    - <b>Markov-property</b>: P(s'|s,a) transition probability matrix. What will be the next s' state after the agent makes action a while being in the state s
    - P(s(t+1)| s(t), s(t-1), s(t-2)...) = P(s(t+1) | s(t))
4. R(s, s'): the reward function of transitioning from state s to s'
5. $\gamma$ gamma discount factor [0, 1]: we perfer rewards now not the future. So, apply the discount to the future rewards.   
    - What would you choose? You get $1000 today or in 10 year's time?
    - discount factor 0.9 -> 0.9 * $1000 = $900 in 10 years
    - It makes the algorithm "greedy" which prefers the current profit instead of future one.

## 32. Exploration vs. Exploitation Problem

In [3]:
# N-armed Bandit Problem

from numpy.random import random
from random import randint

# Epsilon greedy strategy the agent visit new states with epsilon probability
EPSILON = 0.1

BANDITS = 3  # number of bandits
EPISODES = 10000  # number of iterations

class Bandit:
    def __init__(self, probability):        
        self.q = 0  # Qk(a) stores the mean of rewards
        self.k = 0  # k means the number of action a (so the bandit) was chosen in the past
        self.probability = probability  # probability distribution

    def get_reward(self):
        # rewards can be +1 (win) or 0 (lose)
        if random() < self.probability:
            return 1
        else:
            return 0

class NArmedBandit:
    def __init__(self):
        self.bandits = []
        self.bandits.append(Bandit(0.5))
        self.bandits.append(Bandit(0.6))
        self.bandits.append(Bandit(0.4))
    
    def get_bandit_max_q(self):
        """ We find the bandit with max Q(a) value for the greedy exploitation
            We need the index of the bandit with max Q(a)"""
        max_q_bandit_index = 0
        max_q = self.bandits[max_q_bandit_index].q

        for i in range(1, BANDITS):
            if self.bandits[i].q > max_q:
                max_q = self.bandits[i].q
                max_q_bandit_index = i
        return max_q_bandit_index
    
    def select_bandit(self):
        """ This is the epsilon-greedy strategy with epsilon probability the agent explore
            - otherwise it exploits"""
        if random() < EPSILON:
            bandit_index = randint(0, BANDITS-1)  # exploration
        else:
            bandit_index = self.get_bandit_max_q()  # exploitation
        return bandit_index
    
    def update(self, bandit, reward):  # Q[k+1]
        bandit.k = bandit.k + 1
        bandit.q = bandit.q + (1 / (1 + bandit.k)) * (reward - bandit.q)  # recursive formula
    
    def run(self):
        for i in range(EPISODES):
            bandit = self.bandits[self.select_bandit()]
            reward = bandit.get_reward()
            self.update(bandit, reward)
            print(f'Iteration {i}, bandit {bandit.probability} with Q value {bandit.q}')
    
    def show_stat(self):
        for i in range(BANDITS):
            print(f'Bandit {i} with k: {self.bandits[i].k}')  


In [4]:
bandit_problem = NArmedBandit()
bandit_problem.run()
bandit_problem.show_stat()

Iteration 0, bandit 0.5 with Q value 0.5
Iteration 1, bandit 0.5 with Q value 0.33333333333333337
Iteration 2, bandit 0.5 with Q value 0.25
Iteration 3, bandit 0.5 with Q value 0.2
Iteration 4, bandit 0.5 with Q value 0.33333333333333337
Iteration 5, bandit 0.5 with Q value 0.4285714285714286
Iteration 6, bandit 0.5 with Q value 0.5
Iteration 7, bandit 0.5 with Q value 0.4444444444444444
Iteration 8, bandit 0.5 with Q value 0.39999999999999997
Iteration 9, bandit 0.5 with Q value 0.45454545454545453
Iteration 10, bandit 0.5 with Q value 0.41666666666666663
Iteration 11, bandit 0.5 with Q value 0.3846153846153846
Iteration 12, bandit 0.6 with Q value 0.0
Iteration 13, bandit 0.5 with Q value 0.42857142857142855
Iteration 14, bandit 0.6 with Q value 0.3333333333333333
Iteration 15, bandit 0.5 with Q value 0.4666666666666666
Iteration 16, bandit 0.5 with Q value 0.49999999999999994
Iteration 17, bandit 0.5 with Q value 0.4705882352941176
Iteration 18, bandit 0.5 with Q value 0.44444444444

## Q-learning

<b>Value-iteration</b> and <b>Policy-iteration</b>
- These are two fundamental methods for solving MDPs
- Assumes that the agent knows the MDP model of the world such as 
    - <b>P(s'| s, a)</b> probability distribution
    - <b>R(s', s)</b> reward function
- It is an offline-learning: the agent can plan its actions given knowledge about the environment before interacting with it.

<b>Q-Learning</b>
- It is a <i>model-free</i> approach
- The agent knows nothing about the underlying MDP model
- The agent knows the possible states and actions exclusively
- It is an online-learning: the agent improves its behavior through learning from the history of interactions with the environment.


Since, Q-learning does not know the underlying model, it uses the time-difference learning concept.
- Q(s, a) = Q(s, a) + $\alpha$[R(s, a) + $\gamma$ maxQ(s', a') - Q(s, a)]
    - a' =  R(s, a) + $\gamma$ maxQ(s', a')
    - it is an online-algorithm: we can update Q(s, a) as soon as we know s'
    - if $\alpha$ = 1 then we end up with the Bellman-equation
    - The learning rate controls how much of the difference between previous Q(s, a) value and newly proposed Q(s', a') value s taken into account
- The following is the rearranged formula we usually use for Q-learning
    -  Q(s, a) = (1-$\alpha$) Q(s, a) + $\alpha$[R(s, a) + $\gamma$ maxQ(s', a')]

### Q-Learning Algorithm

1. Initialization: $\gamma$ gamma, $\alpha$ alpha and R reward matrix + Q(s, a) matrix with <b>Zero</b> 
2. For each episode
    1. select a random initial state
    2. do while the terminal state hasn't been reached
        1. select one among all possible a actions for current s state
        2. use this a action to go the next s' state
        3. calculate the max Q(s', a') value for this next s' state based on all possible actions
            - Q(s, a) = (1-$\alpha$) Q(s, a) + $\alpha$[R(s, a) + $\gamma$ maxQ(s', a')]
        4. set the next state as the current one so s=s'


## 34. Q Learning Implementation (Tic Tac Toe)

In [7]:
# Q Learning: Tic Tac Toe
import random

BLANK = ' '
AI_PLAYER = 'X'
HUMAN_PLAYER = 'O'

TRAINING_EPOCHS = 40000
TRAINING_EPSILON = .4
REWARD_WIN = 10
REWARD_LOSE = -10
REWARD_TIE = 0


class Player:

    @staticmethod
    def show_board(board):
        print('|'.join(board[0:3]))
        print('|'.join(board[3:6]))
        print('|'.join(board[6:9]))


class HumanPlayer(Player):

    def reward(self, value, board):
        pass

    def make_move(self, board):

        while True:
            try:
                self.show_board(board)
                move = input('Your next move (cell index 1-9):')
                move = int(move)

                if not (move - 1 in range(9)):
                    raise ValueError
            except ValueError:
                print('Invalid move; try again:\n')
            else:
                return move-1

In [8]:
class AIPlayer(Player):

    def __init__(self, epsilon=0.4, alpha=0.3, gamma=0.9, default_q=1):
        self.EPSILON = epsilon  # The probability of exploration
        self.ALPHA = alpha      # Learning Rate
        # discount parameter for future reward (rewards now are better than rewards in the future)
        self.GAMMA = gamma
        # if the given move at the given state is not defined yet: we have a default Q value
        self.DEFAULT_Q = default_q
        
        # Q(s,a) function is a dict in this implementation.
        # This is the Q function - Q: SxA -> R 
        # return a value for s state and a action (s,a) pair
        self.q = {}
        self.move = None  # Previous move during the game
        
        # board in the previous iteration
        self.board = (' ',) * 9

    # there are available or emtpy cells on the grid (board)
    def available_moves(self, board):
        """There are available or empty cells on the grid (board)."""
        return [i for i in range(9) if board[i] == ' ']

    def get_q(self, state, action):
        """Q(s,a) -> Q value for (s,a) pair - if no Q value exists then create a new one with the
           default value (=1) and otherwise we return the q value present in the dict."""

        if self.q.get((state, action)) is None:
            self.q[(state, action)] = self.DEFAULT_Q

        return self.q[(state, action)]


    def make_move(self, board):
        """Make a random move with epsilon probability (exploration) or
           pick the action with the highest Q value (exploitation)."""

        self.board = tuple(board)
        actions = self.available_moves(board)

        # EXPLORATION
        # action with epsilon probability
        if random.random() < self.EPSILON:  # Perform Exploration (Random move)
            # this is in index (0-8 board cell related index)
            self.move = random.choice(actions)
            return self.move

        # EXPLOITATION
        # Take the action with highest Q value
        q_values = [self.get_q(self.board, a) for a in actions]
        max_q_value = max(q_values)

        # if multiple best actions, choose one at random
        if q_values.count(max_q_value) > 1:
            best_actions = [i for i in range(len(actions)) if q_values[i] == max_q_value]
            best_move = actions[random.choice(best_actions)]
        # there is just a single best move (best action)
        else:
            best_move = actions[q_values.index(max_q_value)]

        self.move = best_move
        return self.move

    
    def reward(self, reward, board):
        """reward() evaluate a given state: so update the Q(s, a) table regarding s state and a action."""

        if self.move:
            prev_q = self.get_q(self.board, self.move)  # the state is the board itself
            max_q_new = max([self.get_q(tuple(board), a) for a in self.available_moves(self.board)])
            self.q[(self.board, self.move)] = prev_q + self.ALPHA * (reward + self.GAMMA * max_q_new - prev_q)



In [9]:

class TicTacToe:

    def __init__(self, player1, player2):
        self.player1 = player1
        self.player2 = player2
        self.first_player_turn = random.choice([True, False])
        self.board = [' '] * 9

    def play(self):

        # this is the "game loop"
        while True:
            if self.first_player_turn:
                player = self.player1
                other_player = self.player2
                player_tickers = ('X', 'O')
            else:
                player = self.player2
                other_player = self.player1
                player_tickers = ('O', 'X')

            # check the state of the game (win, lose or draw)
            game_over, winner = self.is_game_over(player_tickers)

            # game is over: handle the rewards
            if game_over:
                if winner == player_tickers[0]:
                    player.show_board(self.board[:])
                    print('\n %s won!' % player.__class__.__name__)
                    player.reward(REWARD_WIN, self.board[:])
                    other_player.reward(REWARD_LOSE, self.board[:])
                if winner == player_tickers[1]:
                    player.show_board(self.board[:])
                    print('\n %s won!' % other_player.__class__.__name__)
                    other_player.reward(REWARD_WIN, self.board[:])
                    player.reward(REWARD_LOSE, self.board[:])
                else:
                    player.show_board(self.board[:])
                    print('Tie!')
                    player.reward(REWARD_TIE, self.board[:])
                    other_player.reward(REWARD_TIE, self.board[:])
                break

            # next player's turn in the next iteration
            self.first_player_turn = not self.first_player_turn

            # actual player's best move (based on Q(s,a) table for AI player)
            move = player.make_move(self.board)
            self.board[move] = player_tickers[0]

    def is_game_over(self, player_tickers):

        # consider both players (X and O players - these are the tickers)
        for player_ticker in player_tickers:

            # check horizontal dimension (so the rows)
            for i in range(3):
                if self.board[3 * i + 0] == player_ticker and\
                        self.board[3 * i + 1] == player_ticker and\
                        self.board[3 * i + 2] == player_ticker:
                    return True, player_ticker

            # check vertical dimension (so the columns)
            for j in range(3):
                if self.board[j + 0] == player_ticker and \
                        self.board[j + 3] == player_ticker and \
                        self.board[j + 6] == player_ticker:
                    return True, player_ticker

            # check diagonal dimensions (top left to bottom right + top right to bottom left)
            if self.board[0] == player_ticker and self.board[4] == player_ticker and\
                self.board[8] == player_ticker:
                return True, player_ticker

            if self.board[2] == player_ticker and self.board[4] == player_ticker and\
                 self.board[6] == player_ticker:
                return True, player_ticker

        # finally we can deal with the 'draw' cases
        if self.board.count(' ') == 0:
            return True, None  # Draw Case
        else:
            return False, None  # Game is not over


In [10]:
# Training

ai_player_1 = AIPlayer()
ai_player_2 = AIPlayer()

print('Training the AI player(s)...')

ai_player_1.EPSILON = TRAINING_EPSILON
ai_player_2.EPSILON = TRAINING_EPSILON

for _ in range(TRAINING_EPOCHS):
    game = TicTacToe(ai_player_1, ai_player_2)
    game.play()

print('\nTraining is Done')

Training the AI player(s)...
X|X|O
O|X|X
X|O|O
Tie!
 |X|X
 |O|X
O|O|O

 AIPlayer won!
O|X|O
O|X|X
O|O|X

 AIPlayer won!
X|O|X
O|X|X
X|O|O

 AIPlayer won!
X| | 
X|O| 
X| |O

 AIPlayer won!
O|O|O
X|X| 
X| |O

 AIPlayer won!
X|O|O
O|X|X
O|X|O
Tie!
O|O| 
 |X|O
X|X|X

 AIPlayer won!
O|X|O
X| |O
X|X|O

 AIPlayer won!
O| |O
 |X|O
X|X|O

 AIPlayer won!
O|X|X
O|X|O
X|O| 

 AIPlayer won!
O| |X
O|X|O
X| |X

 AIPlayer won!
O|X|O
 |X|O
O|X|X

 AIPlayer won!
O|X|X
X|O|O
O|X|O

 AIPlayer won!
 |X|X
O|X|O
O|X|O

 AIPlayer won!
O|X| 
 |O|O
X|X|X

 AIPlayer won!
 | |O
O|O|X
X|X|X

 AIPlayer won!
 |X|X
X|X|O
O|O|O

 AIPlayer won!
O|O|O
X|X|O
X| |X

 AIPlayer won!
O|O|X
X|O|X
O|X|X

 AIPlayer won!
X|X| 
X|O|O
X|O|O

 AIPlayer won!
 |X| 
 |X|O
 |X|O

 AIPlayer won!
 |X|O
 |X| 
O|X| 

 AIPlayer won!
O|O|O
O|X|X
X|X|O

 AIPlayer won!
O|X| 
O|O|O
X|X| 

 AIPlayer won!
 | |O
X|X|X
X|O|O

 AIPlayer won!
X| | 
X|X|O
X|O|O

 AIPlayer won!
X|O|O
O|O| 
X|X|X

 AIPlayer won!
X| |O
X|X|X
 |O|O

 AIPlayer won!
O|X|X
 

In [16]:
ai_player_1.q  # hugh size of dictionary

{((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 0): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 1): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 2): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 3): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 4): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 5): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 6): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 7): 1,
 ((' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' '), 8): 1,
 (('X', 'X', 'O', ' ', ' ', ' ', ' ', 'O', ' '), 3): 1,
 (('X', 'X', 'O', ' ', ' ', ' ', ' ', 'O', ' '), 4): 1,
 (('X', 'X', 'O', ' ', ' ', ' ', ' ', 'O', ' '), 5): 1,
 (('X', 'X', 'O', ' ', ' ', ' ', ' ', 'O', ' '), 6): 1,
 (('X', 'X', 'O', ' ', ' ', ' ', ' ', 'O', ' '), 8): 1,
 (('X', 'X', 'O', 'O', 'X', ' ', ' ', 'O', ' '), 5): 1,
 (('X', 'X', 'O', 'O', 'X', ' ', ' ', 'O', ' '), 6): 1,
 (('X', 'X', 'O', 'O', 'X', ' ', ' ', 'O', ' '), 8): 10.08469243,
 (('X', 'X', 'O', 'O', 'X', ' ', 'X', 

In [17]:
# Play Game
# Epsilon=0 means no exploration - it will use the Q(s,a) function to make the moves
# print(ai_player_1.q)
ai_player_1.EPSILON = 0  # Use only exploitation
human_player = HumanPlayer()
game = TicTacToe(ai_player_1, human_player)
game.play()

 | | 
 |X| 
 | | 
X| | 
 |X| 
 | |O
X| |O
 |X|X
 | |O
X| |O
O|X|X
X| |O
X|O|O
O|X|X
X|X|O
Tie!


## 36. Deep Q Learning (Tic Tac Toe)

- Mario Game: CNN without pooling layer 
    - Because pooling layer makes sure  the network becomes insensitive to the location of an object in the image

In [18]:
# DeepQLearning: Tic Tac Toe

import random
from keras.models import Sequential
from keras.layers import Dense
import numpy as np

BLANK = ' '
AI_PLAYER = 'X'
HUMAN_PLAYER = 'O'
TRAINING_EPOCHS = 20000
TRAINING_EPSILON = 0.4
REWARD_WIN = 10
REWARD_LOSE = -10
REWARD_TIE = 0


class Player:

    @staticmethod
    def show_board(board):
        print('|'.join(board[0:3]))
        print('|'.join(board[3:6]))
        print('|'.join(board[6:9]))


class HumanPlayer(Player):

    def reward(self, value, board):
        pass

    def make_move(self, board):

        while True:
            try:
                self.show_board(board)
                move = input('Your next move (cell index 1-9):')
                move = int(move)
                if not (move - 1 in range(9)):
                    raise ValueError
            except ValueError:
                print('Invalid move; try again:\n')
            else:
                return move - 1

In [19]:
class AIPlayer(Player):

    def __init__(self, epsilon=0.4, alpha=0.3, gamma=0.9, default_q=1):
        self.EPSILON = epsilon  # The probability of exploration
        self.ALPHA = alpha  # Learning Rate
        # discount parameter for future reward (rewards now are better than rewards in the future)
        self.GAMMA = gamma
        # if the given move at the given state is not defined yet: we have a default Q value
        self.DEFAULT_Q = default_q
        
        # the Q(s,a) function is a neural network (this is how we eliminate the huge data structure)
        # single hidden layer with 32 neurons - output is 1 which is the optimal move (so the index)
        # input neurons: 36
        self.q = Sequential()
        self.q.add(Dense(32, input_dim=36, activation='relu'))
        self.q.add(Dense(1, activation='relu'))
        self.q.compile(optimizer='adam', loss='mean_squared_error')

        self.move = None  # Previous move during the game
        
        # board in the previous iteration
        self.board = (' ',) * 9

    def available_moves(self, board):
        """There are available or empty cells on the grid (board)."""

        return [i for i in range(9) if board[i] == ' ']

    def encode_input(self, board, action):
        """The (s,a) pair is represented with a one-dimensional array (one-hot reresentation)"""

        vector_representation = []

        # one-hot encoding for the 3 states
        # [1,0,0] - it means the given cell has X ticker
        # [0,1,0] - it means the given cell has O ticker
        # [0,0,1] - it means the given cell has ' ' ticker so empty
        # every single cell on the board (9 cells) has 3 values because of this representation
        # so there are 9x3=27 values
        for cell in board:
            for ticker in ['X', 'O', ' ']:
                if cell == ticker:
                    vector_representation.append(1)
                else:
                    vector_representation.append(0)

        # one-hot encoding of the action - array with size 9
        # [1,0,0,0,0,0,0,0,0] - it means putting X to the first cell
        # [0,1,0,0,0,0,0,0,0] - it means putting X to the second cell
        for move in range(9):
            if action == move:
                vector_representation.append(1)
            else:
                vector_representation.append(0)

        # all together there are 27+9=36 values (the input layer has 36 neurons)
        return np.array([vector_representation])


    def get_q(self, state, action):
        """Q(s,a) - we have the input (s,a) representation and the neural network will make
           a prediction (returns the Q value - this value will be learned during training)."""

        return self.q.predict([self.encode_input(state, action)], batch_size=1)


    def make_move(self, board):
        """Make a random move with epsilon probability (exploration) or
           pick the action with the highest Q value (exploitation)."""

        self.board = tuple(board)
        actions = self.available_moves(board)

        # action with epsilon probability
        if random.random() < self.EPSILON:  # Perform Exploration (Random move)
            # this is in index (0-8 board cell related index)
            self.move = random.choice(actions)
            return self.move

        # Take the action with highest Q value
        q_values = [self.get_q(self.board, a) for a in actions]
        max_q_value = max(q_values)

        # if multiple best actions, choose one at random
        if q_values.count(max_q_value) > 1:
            best_actions = [i for i in range(len(actions)) if q_values[i] == max_q_value]
            best_move = actions[random.choice(best_actions)]
        # there is just a single best move (best action)
        else:
            best_move = actions[q_values.index(max_q_value)]

        self.move = best_move
        return self.move

    
    def reward(self, reward, board):
        """reward() evaluate a given state: so update the Q(s, a) table regarding s state and a action."""

        if self.move:
            prev_q = self.get_q(self.board, self.move)
            max_q_new = max([self.get_q(tuple(board), a) for a in self.available_moves(self.board)])
            
            # Train the neural network with the new (s,a) and Q value
            self.q.fit(self.encode_input(self.board, self.move),  # Feature
                       prev_q + self.ALPHA * ((reward + self.GAMMA * max_q_new) - prev_q),  # Target 
                       epochs=3, verbose=0)

        self.move = None
        self.board = None

In [20]:
class TicTacToe:

    def __init__(self, player1, player2):
        self.player1 = player1
        self.player2 = player2
        self.first_player_turn = random.choice([True, False])
        self.board = [' '] * 9

    def play(self):

        # this is the "game loop"
        while True:
            if self.first_player_turn:
                player = self.player1
                other_player = self.player2
                player_tickers = ('X', 'O')
            else:
                player = self.player2
                other_player = self.player1
                player_tickers = ('O', 'X')

            # check the state of the game (win, lose or draw)
            game_over, winner = self.is_game_over(player_tickers)

            # game is over: handle the rewards
            if game_over:
                if winner == player_tickers[0]:
                    player.show_board(self.board[:])
                    print('\n %s won!' % player.__class__.__name__)
                    player.reward(REWARD_WIN, self.board[:])
                    other_player.reward(REWARD_LOSE, self.board[:])
                if winner == player_tickers[1]:
                    player.show_board(self.board[:])
                    print('\n %s won!' % other_player.__class__.__name__)
                    other_player.reward(REWARD_WIN, self.board[:])
                    player.reward(REWARD_LOSE, self.board[:])
                else:
                    player.show_board(self.board[:])
                    print('Tie!')
                    player.reward(REWARD_TIE, self.board[:])
                    other_player.reward(REWARD_TIE, self.board[:])
                break

            # next player's turn in the next iteration
            self.first_player_turn = not self.first_player_turn

            # actual player's best move (based on Q(s,a) table for AI player)
            move = player.make_move(self.board)
            self.board[move] = player_tickers[0]

    def is_game_over(self, player_tickers):

        # consider both players (X and O players - these are the tickers)
        for player_ticker in player_tickers:

            # check horizontal dimension (so the rows)
            for i in range(3):
                if self.board[3 * i + 0] == player_ticker and\
                        self.board[3 * i + 1] == player_ticker and\
                        self.board[3 * i + 2] == player_ticker:
                    return True, player_ticker

            # check vertical dimension (so the columns)
            for j in range(3):
                if self.board[i + 0] == player_ticker and\
                        self.board[i + 3] == player_ticker and\
                        self.board[i + 6] == player_ticker:
                    return True, player_ticker

            # check diagonal dimensions (top left to bottom right + top right to bottom left)
            if self.board[0] == player_ticker and self.board[4] == player_ticker and self.board[8] == player_ticker:
                return True, player_ticker

            if self.board[2] == player_ticker and self.board[4] == player_ticker and self.board[6] == player_ticker:
                return True, player_ticker

        # finally we can deal with the 'draw' cases
        if self.board.count(' ') == 0:
            return True, None  # Draw Case
        else:
            return False, None  # Game is not over

In [21]:
# Training
ai_player_1 = AIPlayer()
ai_player_2 = AIPlayer()

print('Training')
ai_player_1.EPSILON = TRAINING_EPSILON
ai_player_1.EPSILON = TRAINING_EPSILON

for i in range(TRAINING_EPOCHS):
    print("Training iteration %s" % i)
    game = TicTacToe(ai_player_1, ai_player_2)
    game.play()

print('\nTraining is Done')

Training
Training iteration 0
1/1 [==============================] - 0s 18ms/step
O| |X
O|X|O
X| |X

 AIPlayer won!
1/1 [==============================] - 0s 17ms/step
Training iteration 1
1/1 [==============================] - 0s 16ms/step
X|O|X
X|O|O
X|X|O
Tie!
1/1 [==============================] - 0s 15ms/step
Training iteration 2
1/1 [==============================] - 0s 17ms/step
O|X|O
O|X|O
X|O|X
Tie!
1/1 [==============================] - 0s 15ms/step
Training iteration 3
1/1 [==============================] - 0s 16ms/step
O|O|X
X|X|O
O|O|X
Tie!
1/1 [==============================] - 0s 17ms/step
Training iteration 4
1/1 [==============================] - 0s 18ms/step
O|O|X
X|O|X
O|X|O

 AIPlayer won!
1/1 [==============================] - 0s 17ms/step
Training iteration 5
1/1 [==============================] - 0s 17ms/step
X|O|X
O|O|O
X|X| 

 AIPlayer won!
1/1 [==============================] - 0s 18ms/step
Training iteration 6
1/1 [==============================] - 0s 14ms/st

In [5]:
# Play Game
# Epsilon=0 means no exploration - it will use the Q(s,a) function to make the moves
ai_player_1.EPSILON = 0
human_player = HumanPlayer()
game = TicTacToe(ai_player_1, human_player)
game.play()


1/1 [==============================] - 0s 19ms/step
X| | 
 | | 
 | | 
1/1 [==============================] - 0s 17ms/step
X| | 
 |O| 
 | |X
1/1 [==============================] - 0s 18ms/step
X| |O
 |O|X
 | |X
X| |O
 |O|X
O| |X

 HumanPlayer won!
1/1 [==============================] - 0s 17ms/step
